## retrieve atlas probes

In [1]:
import requests

def get_from_atlas(url):
    response = requests.get(url).json()
    while True:
        for anchor in response["results"]:
            yield anchor

        if response["next"]:
            response = requests.get(response["next"]).json()
        else:
            break

In [2]:
import pickle

raw_atlas_probe_file = "../datasets/raw_probe_atlas.pickle"

anchors = {}
for index, anchor in enumerate(get_from_atlas("https://atlas.ripe.net/api/v2/probes/")):

    # filter probes based on generic criteria
    if (
        anchor["status"]["name"] != "Connected"
        or anchor.get("geometry") is None
        or anchor.get("address_v4") is None
        or anchor.get("country_code") is None
    ):
        continue


    anchors[anchor["address_v4"]] = {
        "id" : anchor["id"],
        "is_anchor" : anchor["is_anchor"],
        "country_code" : anchor["country_code"],
        "latitude" : anchor["geometry"]["coordinates"][1],
        "longitude" : anchor["geometry"]["coordinates"][0],
    }

print(f"Number of Atlas probes kept: {len(anchors)}/{index}")

for i, (anchor, anchor_description) in enumerate(anchors.items()):
    if i > 10: break
    print(f"anchor {anchor}:", anchor_description)

# save results
with open(raw_atlas_probe_file, "wb") as f:
    pickle.dump(anchors,f)

Number of Atlas probes kept: 10910/46005
anchor 45.138.229.91: {'id': 60052, 'is_anchor': False, 'country_code': 'NL', 'latitude': 52.3685, 'longitude': 4.8995}
anchor 77.174.76.85: {'id': 10003, 'is_anchor': False, 'country_code': 'NL', 'latitude': 52.3685, 'longitude': 4.9375}
anchor 82.217.219.124: {'id': 7, 'is_anchor': False, 'country_code': 'NL', 'latitude': 51.2005, 'longitude': 6.0075}
anchor 83.81.82.33: {'id': 8, 'is_anchor': False, 'country_code': 'NL', 'latitude': 51.2315, 'longitude': 6.0375}
anchor 193.0.0.78: {'id': 15, 'is_anchor': False, 'country_code': 'NL', 'latitude': 52.3795, 'longitude': 4.8975}
anchor 87.3.187.45: {'id': 14, 'is_anchor': False, 'country_code': 'IT', 'latitude': 41.8995, 'longitude': 12.4375}
anchor 77.174.30.45: {'id': 20, 'is_anchor': False, 'country_code': 'NL', 'latitude': 52.0075, 'longitude': 5.9585}
anchor 93.108.63.51: {'id': 24, 'is_anchor': False, 'country_code': 'PT', 'latitude': 38.7295, 'longitude': -9.1515}
anchor 86.89.224.211: {'id

## generate iris probing file

In [3]:
from pathlib import Path
import pickle
import csv

raw_atlas_probe_file = Path(".") / "../datasets/raw_probe_atlas.pickle"
probing_file = Path(".") / "../datasets/iris_ping_probing.csv"

# get probes dataset
with open(raw_atlas_probe_file, "rb") as f:
    probes_atlas = pickle.load(f)

# generate probing file
with open(probing_file, "w") as f:
    csv_writer = csv.writer(f)
    for probe in probes_atlas:
        row = [str(probe) + '/32', "icmp",2,50,1]
        csv_writer.writerow(row)

## iris probing

In [1]:
from datetime import datetime
from uuid import UUID
from pathlib import Path

from geoloc_imc_2023.iris_probing import IrisProber

ping_probing_rate = 10_000
date = datetime.today().strftime("%Y-%m-%d-%H-%M-%S")
tags = [f"atlas-ping-{date}-{ping_probing_rate}"]
agent_uuids = {
    UUID("ddd8541d-b4f5-42ce-b163-e3e9bfcd0a47"): ping_probing_rate,
}
probing_file = Path(".") / "../datasets/iris_ping_probing.csv"

iris_prober = IrisProber(
    tags=tags,
    tool="ping",
    input_file_path=probing_file,
    probing_rates=agent_uuids,
    idle_time=180,
)

print("starting measurements")
measurement_uuid = iris_prober.probe()
iris_prober.wait_until_complete(measurement_uuid)

print(measurement_uuid)

starting measurements
f5be1305-9bb9-4018-8093-ac0f8fd3c7a4


## retreive results

In [2]:
from geoloc_imc_2023.iris_probing import PingResults

measurement_uuid = "f5be1305-9bb9-4018-8093-ac0f8fd3c7a4"
raw_results = PingResults(measurement_uuid).query("ddd8541d-b4f5-42ce-b163-e3e9bfcd0a47")

In [4]:
import pickle
from pathlib import Path

responsive_probe_atlas_file = Path(".") / "../datasets/responsive_probe_atlas.pickle"
raw_atlas_probe_file = Path(".") / "../datasets/raw_probe_atlas.pickle"

with open(raw_atlas_probe_file, "rb") as f:
    raw_atlas_probe = pickle.load(f)

responsive_probes = {}
unresponsive_ip = 0
for row in raw_results:

    probe_dst = row['probe_dst_addr'].split(":")[-1]
    rtt = row['rtt']

    try:
        probe_description = raw_atlas_probe[probe_dst]
    except KeyError:
        unresponsive_ip += 1
        continue

    responsive_probes[probe_dst] = probe_description

print(f"Number of Atlas probes kept: {len(responsive_probes)}, rejected : {len(raw_atlas_probe)-len(responsive_probes) }")

# save results
with open(responsive_probe_atlas_file, "wb") as f:
    pickle.dump(responsive_probes,f)

Number of Atlas probes kept: 7193, rejected : 3717


## get country goeloc dataset

In [7]:
import csv
import pandas as pd
from pathlib import Path

countries_file = Path(".") / "../datasets/countries.txt"
out_file = Path(".") / "../datasets/countries.pickle"

countries = {}
with open(countries_file, "r") as f:
    for i, row in enumerate(f.readlines()):

        row = [value.strip() for value in row.split(" ")]
        countries[row[0]] = {
            "latitude": row[1],
            "longitude": row[2],
            "name": row[3],
        }

for i, (country_code, geoloc) in enumerate(countries.items()):
    if i > 10: break
    print(f"{country_code} : {geoloc}")

# save results
with open(out_file, "wb") as f:
    pickle.dump(countries,f)

AD : {'latitude': '42.546245', 'longitude': '1.601554', 'name': 'Andorra'}
AE : {'latitude': '23.424076', 'longitude': '53.847818', 'name': 'United'}
AF : {'latitude': '33.93911', 'longitude': '67.709953', 'name': 'Afghanistan'}
AG : {'latitude': '17.060816', 'longitude': '-61.796428', 'name': 'Antigua'}
AI : {'latitude': '18.220554', 'longitude': '-63.068615', 'name': 'Anguilla'}
AL : {'latitude': '41.153332', 'longitude': '20.168331', 'name': 'Albania'}
AM : {'latitude': '40.069099', 'longitude': '45.038189', 'name': 'Armenia'}
AN : {'latitude': '12.226079', 'longitude': '-69.060087', 'name': 'Netherlands'}
AO : {'latitude': '-11.202692', 'longitude': '17.873887', 'name': 'Angola'}
AQ : {'latitude': '-75.250973', 'longitude': '-0.071389', 'name': 'Antarctica'}
AR : {'latitude': '-38.416097', 'longitude': '-63.616672', 'name': 'Argentina'}


## eliminate default geoloc probes

In [8]:
import pickle
from geoloc_imc_2023.helpers import distance

responsive_probes_file = "../datasets/responsive_probe_atlas.pickle"
probe_atlas_file = "../datasets/probes_atlas.pickle"
countries_file = "../datasets/countries.pickle"

countries = {}
with open(countries_file,"rb") as f:
    countries = pickle.load(f)

responsive_probes = {}
with open(responsive_probes_file,"rb") as f:
    responsive_probes = pickle.load(f)


anchors = {}
for anchor, anchor_description in responsive_probes.items():

    # check if probe coordinates are close to default location
    try:
        country_geo = countries[anchor_description["country_code"]]
    except KeyError as e:
        print(f"error country code {country_code} is unknown")
        continue

    # if the country code is unknown, remove probe from dataset
    country_lat = float(country_geo["latitude"])
    country_lon = float(country_geo["longitude"])

    probe_lat = float(anchor_description["latitude"])
    probe_lon = float(anchor_description["longitude"])

    dist = distance(country_lat, probe_lat,country_lon, probe_lon)

    if dist > 5: anchors[anchor] = anchor_description

print(f"Number of Atlas probes kept: {len(anchors)}, rejected: {len(responsive_probes)- len(anchors)}")

# save results
with open(probe_atlas_file, "wb") as f:
    pickle.dump(anchors,f)

error country code AS is unknown
error country code AS is unknown
error country code AS is unknown
error country code AS is unknown
Number of Atlas probes kept: 7135, rejected: 58


## get passive measurements

In [9]:
def get_measurement(url):
    response = requests.get(url).json()
    while True:
        for anchor in response["results"]:
            yield anchor

        if response["next"]:
            response = requests.get(response["next"]).json()
        else:
            break

In [5]:
import pickle
import requests
import time

from collections import defaultdict
from json import JSONDecodeError

anchors_file = "../datasets/anchors.pickle"
anchors_measurement_file = "../datasets/anchor_measurements_file.pickle"

with open(anchors_file, "rb") as f:
    anchors = pickle.load(f)

# load already existing measurements
try:
    with open(anchors_measurement_file, "rb") as f:
        anchor_measurements = pickle.load(f)
except FileNotFoundError:
    anchor_measurements = defaultdict(dict)


def get_measurement_result(url, max_retry: int =60):
    for _ in range(max_retry):
        response = requests.get(url).json()
        if response:
            return response
        time.sleep(2)

print(f"{len(anchor_measurements)} probes were already treated")
try:
    for i, (anchor_addr, probe_description) in enumerate(anchors.items()):
        if i > 10: break

        if anchor_addr in anchor_measurements: continue

        anchor_measurements[anchor_addr] = defaultdict(list)

        print(f"getting measurements for {anchor_addr}")

        url = f"https://atlas.ripe.net/api/v2/measurements/ping/?target_ip={anchor_addr}"
        try:
            resp = requests.get(url, timeout=350).json()
        except JSONDecodeError:
            print(f"could not retreive results for probe: {anchor_addr}")
            time.sleep(5)
            continue

        for i, measurement in enumerate(resp['results']):

            # limit to ten meaasurements
            if i > 10: break

            url = measurement['result']
            results = get_measurement_result(url)

            for result in results:

                if 'src_addr' not in result:
                    continue

                # only keep measurement where there is more than one packet sent
                keys = [list(r.keys())[0] for r in result['result']]

                # extract RTTs from results
                rtt_list = []
                for r in result['result']:
                    try:
                        rtt_list.append(r['rtt'])
                    except KeyError:
                        continue
                print(rtt_list)

                # save RTT between the two probes
                try:
                    anchor_measurements[anchor_addr][result['src_addr']].extend(rtt_list)
                except KeyError:
                    anchor_measurements[anchor_addr][result['src_addr']] = rtt_list
        
            time.sleep(2)

    print(f"atlas measurement retreived for {len(anchor_measurements)} probes")

except KeyboardInterrupt:
    print("interrupted")
    pass

with open(anchors_measurement_file, "wb") as f:
    pickle.dump(anchor_measurements, f)

2 probes were already treated
getting measurements for 5.28.0.17
interrupted


In [22]:
import pickle
import requests
import time

from collections import defaultdict
from json import JSONDecodeError

anchors_file = "../datasets/anchors.pickle"
anchors_measurement_file = "../datasets/anchor_measurements_file.pickle"

with open(anchors_file, "rb") as f:
    anchors = pickle.load(f)

# load already existing measurements
try:
    with open(anchors_measurement_file, "rb") as f:
        anchor_measurements = pickle.load(f)
except FileNotFoundError:
    anchor_measurements = defaultdict(dict)

starting_point = 52592569
starting_point = 52592469
starting_point = 52592369
starting_point = 52592269
starting_point = 52592069
starting_point = 52591869
starting_point = 52591669


def get_results(measurement_id, max_retry: int =10):
    for _ in range(max_retry):
        response = requests.get(
            "https://atlas.ripe.net/api/v2/"
            f"measurements/{measurement_id}/results/"
        ).json()

        if response:
            return response
        time.sleep(2)


print(f"{len(anchor_measurements)} probes were already treated")
try:
    for id in reversed(range(starting_point - 200, starting_point)):
        print(id)

        id_done = []
        for dst_addr in anchor_measurements:
            id_done.extend(anchor_measurements[dst_addr]["id"])

        if id in id_done:
            print("id:", id, "already retrieved")
            continue

        response = get_results(id)
        measurement_results = []

        if not response: continue

        # parse response
        for result in response:

            if type(result) is str:
                print(result)
                continue
            # parse results and calculate geoloc
            if result.get('result') is not None:
                
                dst_addr = result['dst_addr']
                vp_ip = result['from']

                if type(result['result']) == list:
                    rtt_list = [list(rtt.values())[0] for rtt in result['result']]
                else:
                    rtt_list = [result['result']["rtt"]]

                # remove stars from results
                rtt_list = list(filter(lambda x: x != "*", rtt_list))
                if not rtt_list: 
                    continue
                
                # get min rtt
                min_rtt = min(rtt_list)
                if type(min_rtt) is str: 
                    print(min_rtt)
                    continue

                # both vp and target coordinates
                try:
                    vp_lat = anchors[vp_ip]['latitude']
                    vp_lon = anchors[vp_ip]['longitude']
                except KeyError:
                    continue
                
                measurement_results.append({
                    "node": vp_ip,
                    "min_rtt": min_rtt,
                    "rtt_list": rtt_list,
                    "vp_lat": vp_lat,
                    "vp_lon": vp_lon,
                })

            else:
                print(f"no results: {result}")

        measurement_results = sorted(measurement_results, key = lambda x: x["min_rtt"])
        print(dst_addr, ":", len(measurement_results), measurement_results)
        try:
            anchor_measurements[dst_addr]["result"].append(measurement_results)
            anchor_measurements[dst_addr]["ids"].append(id)
        except KeyError:
            anchor_measurements[dst_addr]["result"] = [measurement_results]
            anchor_measurements[dst_addr]["id"] = [id]
        
        print(len(anchor_measurements[dst_addr]["id"]))
            
except KeyboardInterrupt:
    pass
with open(anchors_measurement_file, "wb") as f:
    pickle.dump(anchor_measurements, f)

    

757 probes were already treated
52591668
185.33.216.12 : 777 [{'node': '85.197.82.113', 'min_rtt': 4.580516, 'rtt_list': [4.606864, 4.623924, 4.580516], 'vp_lat': 50.1115, 'vp_lon': 8.7395}, {'node': '91.240.92.5', 'min_rtt': 9.978556, 'rtt_list': [10.030426, 10.060702, 9.978556], 'vp_lat': 51.2705, 'vp_lon': 6.8175}, {'node': '194.122.76.250', 'min_rtt': 10.151204, 'rtt_list': [10.35892, 10.240047, 10.151204], 'vp_lat': 52.3695, 'vp_lon': 4.8995}, {'node': '195.191.197.68', 'min_rtt': 10.336914, 'rtt_list': [10.367328, 10.336914, 10.399761], 'vp_lat': 51.2705, 'vp_lon': 6.8175}, {'node': '185.145.196.198', 'min_rtt': 10.393512, 'rtt_list': [10.420201, 10.482524, 10.393512], 'vp_lat': 50.1275, 'vp_lon': 8.5975}, {'node': '185.178.172.32', 'min_rtt': 11.27657, 'rtt_list': [11.339341, 11.355311, 11.27657], 'vp_lat': 50.0785, 'vp_lon': 14.5205}, {'node': '88.86.103.5', 'min_rtt': 11.287189, 'rtt_list': [11.287189, 11.411992, 11.468212], 'vp_lat': 50.0595, 'vp_lon': 14.4795}, {'node': '93.

In [3]:
import pickle
import requests
import time
from copy import deepcopy

from collections import defaultdict
from json import JSONDecodeError

anchors_file = "../datasets/anchors.pickle"
anchors_measurement_file = "../datasets/anchor_measurements_file.pickle"

with open(anchors_file, "rb") as f:
    anchors = pickle.load(f)

# load already existing measurements
try:
    with open(anchors_measurement_file, "rb") as f:
        anchor_measurements = pickle.load(f)
except FileNotFoundError:
    anchor_measurements = defaultdict(dict)

filtered_results = deepcopy(anchor_measurements)
print("retreived : ", len(anchor_measurements))
for i, anchor in enumerate(filtered_results):
    if len(anchor_measurements[anchor]['result']) == 1:
        if len(anchor_measurements[anchor]['result'][0]) == 0:
            anchor_measurements.pop(anchor)
            print("no results for anchor", anchor)
    else: 
        print("more than one result")
    
    if anchor not in anchors: 
        anchor_measurements.pop(anchor)
    # for index, node_results in enumerate(anchor_measurements[anchor]['result'][0]):
    #     if index > 10: break
    #     print(node_results)
    # print()

with open(anchors_measurement_file, "wb") as f:
    pickle.dump(anchor_measurements, f)


retreived :  784


## select probes with enough measurements

In [ ]:
with open(measurement_out_file, "rb") as f:
    atlas_measurement = pickle.load(f)

print(len(atlas_measurement))

filtered_measurements = {}
unchecked_probes = {}
for target_ip, measurements in atlas_measurement.items():
    i = 0
    for vp, rtt_list in measurements.items():
        if len(rtt_list) > 3:
            # only keep the minimum rtt
            filtered_measurements[target_ip][vp] = min(rtt_list)

    # check that we have measurements from more that one vp
    if len(measurements) < 3:
        filtered_measurements.pop(target_ip)
        unchecked_probes[target_ip] = measurements

    print(f"target ip: {target_ip}, nb_measurements: {len(filtered_measurements[target_ip])}")


print(f"atlas probes with passive measurements: {len(filtered_measurements)}, unchecked probes: {len(unchecked_probes)}")

107
45.138.229.91 : number of measurement with more than one packet: 15
77.174.76.85 : number of measurement with more than one packet: 1
82.217.219.124 : number of measurement with more than one packet: 0
83.81.82.33 : number of measurement with more than one packet: 0
193.0.0.78 : number of measurement with more than one packet: 284
79.12.239.224 : number of measurement with more than one packet: 0
77.174.30.45 : number of measurement with more than one packet: 0
93.108.63.51 : number of measurement with more than one packet: 0
86.89.224.211 : number of measurement with more than one packet: 0
216.147.121.123 : number of measurement with more than one packet: 0
76.82.152.84 : number of measurement with more than one packet: 0
2.57.252.147 : number of measurement with more than one packet: 1
81.220.141.64 : number of measurement with more than one packet: 0
85.225.8.64 : number of measurement with more than one packet: 0
88.163.164.208 : number of measurement with more than one packet

In [ ]:
# check if ips in results are within atlas probes set
for dst, measurements in atlas_measurement.items():
    for src, rtt_list in measurements.items():
        if src in probes_atlas.keys():
            src_latitude = probes_atlas[src][2]
            src_longitude = probes_atlas[src][3]

            dst_latitude = probes_atlas[dst][2]
            dst_longitude = probes_atlas[dst][3]

            dist = distance(
                lat1=float(src_latitude),
                lon1=float(src_longitude),
                lat2=float(dst_latitude),
                lon2=float(dst_longitude),
            )

            print(f"geoloc src: {src}=[{src_latitude}, {src_longitude}] | geoloc dst: {probes_atlas[dst][:]} |rtt = {min(rtt_list)} | dist = {dist}")


geoloc src: 46.183.219.225=[56.9515, 24.1115] | geoloc dst: [60052, False, 52.3685, 4.8995] |rtt = 35.99373 | dist = 1330.9468631458333
geoloc src: 185.114.152.90=[42.3485, -71.0615] | geoloc dst: [60052, False, 52.3685, 4.8995] |rtt = 95.445672 | dist = 5558.333526642797
geoloc src: 192.172.226.235=[32.8815, -117.2415] | geoloc dst: [60052, False, 52.3685, 4.8995] |rtt = 158.975832 | dist = 9002.09353065142
geoloc src: 213.192.184.42=[60.2015, 24.9295] | geoloc dst: [60052, False, 52.3685, 4.8995] |rtt = 33.994832 | dist = 1502.5986617113351
geoloc src: 197.239.73.59=[12.3715, -1.5085] | geoloc dst: [60052, False, 52.3685, 4.8995] |rtt = 112.793753 | dist = 4484.270724323151
geoloc src: 185.233.100.99=[44.8575, -0.5615] | geoloc dst: [60052, False, 52.3685, 4.8995] |rtt = 23.913838 | dist = 926.0231243763532
geoloc src: 196.49.14.25=[5.5975, -0.1885] | geoloc dst: [60052, False, 52.3685, 4.8995] |rtt = 119.303678 | dist = 5221.602307864207
geoloc src: 78.141.215.164=[52.3885, 4.6605] 

In [ ]:
measurement_file = "../datasets/measurement_atlas.pickle"

with open(measurement_file, "wb") as f:
    pickle.dump(atlas_measurement, f)

## verify probe location based on measurements

In [ ]:
# first method, simple, check if RTT coherent for all probes

# load everything (testing)
probes_path = Path(".") / "../datasets/probe_atlas.pickle"

with open(probes_path, "rb") as f:
    probes_atlas = pickle.load(f)


measurement_path = Path(".") / "../datasets/measurement_atlas.pickle"

with open(measurement_path, "rb") as f:
    measurement_atlas = pickle.load(f)

In [ ]:
from copy import deepcopy

filtered_measurements = deepcopy(atlas_measurement)
for dst, measurements in atlas_measurement.items():
    for src, rtt_list in measurements.items():
        if len(rtt_list) <= 1:
            # remove measurement where only one packet was sent
            filtered_measurements[dst].pop(src)

filtered_probes = deepcopy(filtered_measurements)
for dst, measurements in filtered_measurements.items():
    if len(measurements) <= 1:
        # remove destination if not enough measurements
        filtered_probes.pop(dst)

print(f"over all probes analyzed: {len(atlas_measurement)}, only {len(filtered_probes)} kept")

over all probes analyzed: 4, only 2 kept


## compare dist / rtt

In [ ]:
from analysis.helpers import rtt_to_km

percentage_dist_similarity = {}
for dst, measurements in filtered_probes.items():
    percentage_dist_similarity[dst] = []
    print(f"VALIDATION FOR PROBE : {dst}")
    for src, rtt_list in measurements.items():
        rtt_dist,dist = None, None
        if src in probes_atlas.keys():
            src_latitude = probes_atlas[src][2]
            src_longitude = probes_atlas[src][3]

            dst_latitude = probes_atlas[dst][2]
            dst_longitude = probes_atlas[dst][3]

            # get distance from lat-lon
            dist = distance(
                lat1=float(src_latitude),
                lon1=float(src_longitude),
                lat2=float(dst_latitude),
                lon2=float(dst_longitude),
            )

            # get distance from rtt
            rtt_dist = rtt_to_km(min(rtt_list))

            similarity = dist * 100 / rtt_dist
            percentage_dist_similarity[dst].append(similarity)

            print(f"src: {src}, rtt : {round(min(rtt_list),2)}, dist : {round(dist,2)}, dist (from rtt) : {round(rtt_dist,2)} ([{round(similarity)}% of similarity])")
    print(f"overall similarity (over {len(measurements)}) : {round(min(percentage_dist_similarity[dst]),2)}")
    print()


VALIDATION FOR PROBE : 45.138.229.91
src: 37.10.126.72, rtt : 144.52, dist : 8940.29, dist (from rtt) : 9634.64 ([93% of similarity])
src: 37.10.41.14, rtt : 240.05, dist : 10486.81, dist (from rtt) : 16003.25 ([66% of similarity])
src: 138.44.176.166, rtt : 341.02, dist : 14147.61, dist (from rtt) : 22734.35 ([62% of similarity])
overall similarity (over 22) : 73.52

VALIDATION FOR PROBE : 193.0.0.78
src: 192.134.1.25, rtt : 16.65, dist : 430.0, dist (from rtt) : 832.52 ([52% of similarity])
src: 193.170.114.242, rtt : 22.6, dist : 934.76, dist (from rtt) : 1129.98 ([83% of similarity])
src: 213.212.129.68, rtt : 23.77, dist : 835.23, dist (from rtt) : 1188.45 ([70% of similarity])
src: 213.128.137.33, rtt : 10.55, dist : 368.66, dist (from rtt) : 527.51 ([70% of similarity])
src: 130.59.80.2, rtt : 22.69, dist : 614.12, dist (from rtt) : 1134.47 ([54% of similarity])
src: 195.30.70.33, rtt : 14.7, dist : 666.25, dist (from rtt) : 735.22 ([91% of similarity])
src: 213.225.160.239, rtt